In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import folium
import os 
import geopy.distance
import geopandas

In [50]:
# DATA

parking=pd.read_csv("data/e-scooter_parks.csv")
park_points=pd.read_csv("data/e-scooter_parks_point.csv")
view=pd.read_csv("data/wdl_od_view.csv")
metro_stops=pd.read_csv("data/metro_stops.txt")
bus_stops=pd.read_csv("data/bus_stops.txt")
metro_stops=metro_stops[["stop_id","stop_name","stop_lat","stop_lon"]]
loc_center = [metro_stops['stop_lat'].mean(), metro_stops['stop_lon'].mean()]  ## mandatory to initialize the map

trips=pd.read_csv("data/trips_bus.txt")




Unnamed: 0  Unnamed: 0.1  objectid_1               toponimo  n_id estado  \
0           0             0         199      Rua de D. Pedro V   204  ATIVO   
1           1             1          32      Rua de D. Pedro V    35  ATIVO   
2           2             2         166  Rua do Passeio Alegre   171  ATIVO   
3           3             3          77  Rua do Passeio Alegre    79  ATIVO   
4           4             4          27   Esplanada do Castelo    30  ATIVO   

  sinal_vert sinal_info_vert  n_lugares         x          y  \
0        NAO             SIM         10 -8.630972  41.149252   
1        NAO             SIM         10 -8.632475  41.147499   
2        NAO             SIM         10 -8.667407  41.147554   
3        NAO             SIM         10 -8.670062  41.148510   
4        NAO             SIM         10 -8.671516  41.148982   

                                       geometry  
0  POINT (-8.630972406820455 41.14925222361455)  
1    POINT (-8.6324746693067 41.14749908119241)  
2  POINT (-8.667406707628464 41.14755430699348)  
3  POINT (-8.670062338817813 41.14850965851483)  
4  POINT (-8.671515945551741 41.14898245215499)

In [51]:
## PORTO MAP
map1 = folium.Map(location = loc_center, tiles='Openstreetmap', zoom_start = 5, control_scale=True)


## PORTO METRO STATIONS ## BLUE POINTS
for index, loc in metro_stops.iterrows():
    folium.Marker([loc['stop_lat'], loc['stop_lon']],color="blue"  , radius=2, weight=5, popup=loc['stop_name']).add_to(map1)
folium.LayerControl().add_to(map1)


## PORTO E_SCOOTER STATIONS ## RED POINTS
for index, loc in parking.iterrows():
    folium.CircleMarker([loc['y'], loc['x']], popup=loc['toponimo'],color="red",  radius=2, weight=15).add_to(map1)
folium.LayerControl().add_to(map1)



## PORTO BUS STATIONS ## BLACK POINTS
for index, loc in bus_stops.iterrows():
    folium.CircleMarker([loc['stop_lat'], loc['stop_lon']],radius=1, weight=5, popup=loc['stop_name'],color="black",fill=False).add_to(map1)
folium.LayerControl().add_to(map1)

map1

In [145]:
#  Giving the geometry coordinate
metro_stop = geopandas.GeoDataFrame(metro_stops,geometry=geopandas.points_from_xy(metro_stops.stop_lon,metro_stops.stop_lat))
bus_stops = geopandas.GeoDataFrame(bus_stops,geometry=geopandas.points_from_xy(bus_stops.stop_lon,bus_stops.stop_lat))


# Providing a type name to each dataframe
metro_stops['type'] = 'metro'
parking['type'] = 'parking'
bus_stops['type'] = 'bus'

# Naming convention
parking['stop_name'] = parking['toponimo']
parking['stop_lat'] = parking['x'] 
parking['stop_lon'] = parking['y'] 

# Concatinating all datasets
df1 = metro_stops[['type','stop_name','stop_lat','stop_lon','geometry']]
df2 = bus_stops[['type','stop_name','stop_lat','stop_lon','geometry']]
df3 = parking[['type','stop_name','stop_lat','stop_lon','geometry']]


# Dataset concatinated row-wise
data = pd.concat([df1, df2, df3])

# Calculating the distances from each metro station (type 'metro' - 84 elements) to each drop-off points ('parking'- 216 elements) in km.

# Here this is done for only one starting point it has to be looped through
# https://www.reddit.com/r/learnpython/comments/c6jpoi/geopydistancedistance_iteration_through_dataframe/


# This results in a dataframe with 84*216 = 18144 rows 


# Next steps 
#  1) filtering the distance < 0.35 km 
#  2) plotting 
    

# The resulting collection of drop-off zones should be kept 
# -> They are in the city center and within reach from the metro stations.

# Question - Should we do the same for bus lines?
#            Were to allocate the remaining drop-off points? 
    


216

In [146]:
data.head()

type          stop_name   stop_lat  stop_lon                   geometry
0  metro  Estadio do Dragao  41.160716 -8.582416  POINT (-8.58242 41.16072)
1  metro           Campanha  41.150537 -8.586245  POINT (-8.58624 41.15054)
2  metro           Heroismo  41.146697 -8.592978  POINT (-8.59298 41.14670)
3  metro       24 de Agosto  41.148796 -8.598349  POINT (-8.59835 41.14880)
4  metro             Bolhao  41.149785 -8.605901  POINT (-8.60590 41.14979)